In [32]:
# Importación de librerías
import pandas as pd
import plotly.express as px
import unidecode
import os

# Ruta del archivo Excel
filePath = '../sdei-annual-pm2-5/sdei-annual-pm2-5-concentrations-countries-urban-areas-v1-1998-2016-xlsx.xlsx'

# Verificar si el archivo existe
if not os.path.exists(filePath):
    print(f"No se encontró el archivo: {filePath}")
    exit()

# Cargar el archivo Excel
excelData = pd.ExcelFile(filePath)

# Información de las hojas a cargar y los detalles de procesamiento
sheet_info = {
    'Country PM2.5 Exceedance': {
        'filter_prefix': 'PMEXDC_',
        'country_column': 'COUNTRY'
    },
    'Urban PM2.5 Exposure': {
        'filter_prefix': 'AVPMU_',
        'country_column': 'COUNTRYENG',
        'city_column': 'STNDRDNAME'
    }
}

# Función para normalizar nombres (países y ciudades)
def normalize_name(name):
    # Convertir a string por si hay valores nulos
    name = str(name)
    # Eliminar tildes y caracteres especiales
    name_without_accents = unidecode.unidecode(name)
    # Convertir a minúsculas y luego capitalizar
    name_formatted = name_without_accents.lower().capitalize()
    return name_formatted

# Función para leer y procesar cada hoja
def load_and_process_sheet(excel_data, sheet_name, filter_prefix, country_column, city_column=None):
    # Cargar la hoja
    df = excel_data.parse(sheet_name)
    
    # Filtrar las columnas que empiezan con el prefijo
    data_columns = [col for col in df.columns if col.startswith(filter_prefix)]
    
    # Renombrar las columnas eliminando el prefijo y espacios
    renamed_columns = {col: col.replace(filter_prefix, '').strip() for col in data_columns}
    df.rename(columns=renamed_columns, inplace=True)
    
    # Crear lista de columnas filtradas (sin prefijos)
    key_columns = [country_column]
    if city_column:
        key_columns.append(city_column)
    filtered_columns = key_columns + list(renamed_columns.values())
    
    # Seleccionar las columnas filtradas
    df = df[filtered_columns]
    
    # Normalizar los nombres de los países y ciudades
    df[country_column] = df[country_column].apply(normalize_name)
    if city_column:
        df[city_column] = df[city_column].apply(normalize_name)
    
    # Renombrar las columnas de país y ciudad para consistencia
    df = df.rename(columns={country_column: 'COUNTRY'})
    if city_column:
        df = df.rename(columns={city_column: 'CITY'})
    
    # Agregar una columna para indicar el indicador (nombre de la hoja)
    df['Indicator'] = sheet_name
    
    # Convertir a formato largo
    id_vars = ['COUNTRY', 'Indicator']
    if city_column:
        id_vars.insert(1, 'CITY')  # Insertar CITY después de COUNTRY
    df_long = pd.melt(df, id_vars=id_vars, var_name='Year', value_name='Value')
    
    # Convertir 'Year' a entero
    df_long['Year'] = df_long['Year'].astype(int)
    
    # Eliminar filas con valores nulos en 'Value'
    df_long = df_long.dropna(subset=['Value'])
    
    return df_long

# Procesar y combinar las hojas seleccionadas
df_list = []
for sheet_name, info in sheet_info.items():
    df_sheet = load_and_process_sheet(
        excel_data=excelData,
        sheet_name=sheet_name,
        filter_prefix=info['filter_prefix'],
        country_column=info['country_column'],
        city_column=info.get('city_column')  # Puede ser None si no está definido
    )
    df_list.append(df_sheet)

# Combinar las hojas en un solo DataFrame
df_combined = pd.concat(df_list, ignore_index=True)

# Función para filtrar datos
def filter_data(df, indicator=None, countries=None, cities=None, start_year=None, end_year=None):
    if indicator is not None:
        df = df[df['Indicator'] == indicator]
    if countries is not None:
        # Normalizar los nombres de los países en el filtro
        countries_normalized = [normalize_name(country) for country in countries]
        df = df[df['COUNTRY'].isin(countries_normalized)]
    if cities is not None and 'CITY' in df.columns:
        # Normalizar los nombres de las ciudades en el filtro
        cities_normalized = [normalize_name(city) for city in cities]
        df = df[df['CITY'].isin(cities_normalized)]
    if start_year is not None:
        df = df[df['Year'] >= start_year]
    if end_year is not None:
        df = df[df['Year'] <= end_year]
    return df

# Función para graficar histograma
def plot_histogram(df, title='Histograma'):
    fig = px.histogram(df, x='Value', nbins=30, title=title)
    fig.update_layout(xaxis_title='Valor', yaxis_title='Frecuencia')
    fig.show()

# Función para graficar mapa
def plot_map(df, year, title='Mapa'):
    # Filtrar por el año especificado
    df_year = df[df['Year'] == year].copy()
    
    # Asegurarnos de que 'Value' es numérico
    df_year['Value'] = pd.to_numeric(df_year['Value'], errors='coerce')
    
    # Eliminar filas con 'Value' nulo
    df_year = df_year.dropna(subset=['Value'])
    
    # Verificar si hay datos de ciudad
    if 'CITY' in df_year.columns:
        # Agrupar por país y calcular la media de 'Value'
        df_grouped = df_year.groupby('COUNTRY')['Value'].mean().reset_index()
    else:
        df_grouped = df_year.groupby('COUNTRY')['Value'].mean().reset_index()
    
    fig = px.choropleth(
        df_grouped,
        locations='COUNTRY',
        locationmode='country names',
        color='Value',
        hover_name='COUNTRY',
        color_continuous_scale=px.colors.sequential.Plasma,
        title=title
    )
    fig.update_geos(showframe=False, projection_type='equirectangular')
    fig.update_layout(legend_title_text='Valor')
    fig.show()


/home/juan27/.local/lib/python3.10/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning:

Cannot parse header or footer so it will be ignored



In [33]:
# Vamos a eliminar las entradas cuyos valores de 'year' sean menores a 2002
df_combined = df_combined[df_combined['Year'] >= 2002]
df_combined 

COUNTRY                 Indicator  Year      Value       CITY
0          Afghanistan  Country PM2.5 Exceedance  2008  13.936634        NaN
1              Albania  Country PM2.5 Exceedance  2008   5.387369        NaN
2              Algeria  Country PM2.5 Exceedance  2008   0.586799        NaN
3       American samoa  Country PM2.5 Exceedance  2008   0.000000        NaN
4              Andorra  Country PM2.5 Exceedance  2008   0.000000        NaN
...                ...                       ...   ...        ...        ...
637614           China      Urban PM2.5 Exposure  2016  13.316667   Zhizhong
637615           China      Urban PM2.5 Exposure  2016  15.050000      Foluo
637616           China      Urban PM2.5 Exposure  2016  14.730000   Huangliu
637617           China      Urban PM2.5 Exposure  2016  14.594737    Chongpo
637618           China      Urban PM2.5 Exposure  2016  17.703448  Tumushuke

[503775 rows x 5 columns]

In [34]:
df_combined.to_json('../datasets/data_filtered_plot.json', orient='records')
df_combined.to_csv('../datasets/data_filtered_plot.csv', index=False)

In [40]:
def plot_city_or_country_data(df, indicator, year, level='city', countries=None):
    """
    Grafica los datos por ciudades o países, ordenados de mayor a menor valor en el eje horizontal.
    
    Parámetros:
    - df: DataFrame con los datos.
    - indicator: Indicador a analizar (por ejemplo, 'Urban PM2.5 Exposure').
    - year: Año a analizar.
    - level: 'city' para graficar por ciudades, 'country' para graficar por países.
    - countries: Lista de países a incluir (opcional). Si es None, se incluyen todos.
    """
    # Validar el parámetro 'level'
    if level not in ['city', 'country']:
        print("El parámetro 'level' debe ser 'city' o 'country'.")
        return
    
    # Normalizar los nombres de los países si se proporcionan
    if countries is not None:
        countries_normalized = [normalize_name(country) for country in countries]
    else:
        countries_normalized = None
    
    # Filtrar los datos según el indicador y el año
    df_filtered = df[
        (df['Indicator'] == indicator) &
        (df['Year'] == year)
    ].copy()
    
    # Filtrar por países si se proporcionan
    if countries_normalized is not None:
        df_filtered = df_filtered[df_filtered['COUNTRY'].isin(countries_normalized)]
    
    # Verificar si se va a graficar por ciudades y si la columna 'CITY' existe
    if level == 'city':
        if 'CITY' not in df_filtered.columns:
            print(f"No hay datos de ciudad para el indicador '{indicator}'.")
            return
        group_field = 'CITY'
    else:
        group_field = 'COUNTRY'
    
    # Asegurarnos de que 'Value' es numérico
    df_filtered['Value'] = pd.to_numeric(df_filtered['Value'], errors='coerce')
    df_filtered = df_filtered.dropna(subset=['Value'])
    
    # Agrupar los datos y calcular la media si es necesario
    df_grouped = df_filtered.groupby(group_field)['Value'].mean().reset_index()
    
    # Ordenar los datos de mayor a menor valor
    df_grouped = df_grouped.sort_values('Value', ascending=False)
    
    # Verificar si hay datos después del filtrado
    if df_grouped.empty:
        print("No hay datos disponibles para los filtros especificados.")
        return
    
    # Crear el gráfico
    fig = px.bar(
        df_grouped,
        x=group_field,
        y='Value',
        title=f"{indicator} en {year} por {'Ciudad' if level == 'city' else 'País'}",
        labels={'Value': 'Valor', group_field: 'Ciudad' if level == 'city' else 'País'}
    )
    fig.update_layout(
        xaxis_title='Ciudad' if level == 'city' else 'País',
        yaxis_title='Valor',
        xaxis_tickangle=-45
    )
    # Actualizar el orden de las categorías en el eje x para reflejar el orden deseado
    fig.update_xaxes(categoryorder='total descending')
    fig.show()


In [36]:
# Ejemplo 1: Filtrar datos y graficar un histograma para ciudades específicas
indicator = 'Urban PM2.5 Exposure'  # Nombre exacto de la hoja
countries = ['Argentina', 'Brasil']
#cities = ['Buenos Aires', 'Rio De Janeiro']
start_year = 2010
end_year = 2015

# Filtrar datos
filtered_df = filter_data(
    df_combined,
    indicator=indicator,
    countries=countries,
    #cities=cities,
    start_year=start_year,
    end_year=end_year
)

# Verificar si el DataFrame no está vacío
if not filtered_df.empty:
    # Graficar histograma
    plot_histogram(filtered_df, title='Exposición Urbana al PM2.5 (2010-2015) en Ciudades Seleccionadas')
else:
    print("No hay datos para los filtros seleccionados.")


In [37]:
# Ejemplo 2: Graficar un mapa para un año específico
indicator = 'Country PM2.5 Exceedance'  # Nombre exacto de la hoja
year = 2008

# Filtrar datos
filtered_df = filter_data(
    df_combined,
    indicator=indicator,
    start_year=year,
    end_year=year
)

# Verificar si el DataFrame no está vacío
if not filtered_df.empty:
    # Graficar mapa
    plot_map(filtered_df, year=year, title='Exceso de PM2.5 por País en 2015')
else:
    print("No hay datos para los filtros seleccionados.")

In [38]:
# Ejemplo 2: Graficar un mapa para un año específico
indicator = 'Urban PM2.5 Exposure'  # Nombre exacto de la hoja
year = 2008

# Filtrar datos
filtered_df = filter_data(
    df_combined,
    indicator=indicator,
    start_year=year,
    end_year=year
)

# Verificar si el DataFrame no está vacío
if not filtered_df.empty:
    # Graficar mapa
    plot_map(filtered_df, year=year, title='Exceso de PM2.5 por País en 2015')
else:
    print("No hay datos para los filtros seleccionados.")

In [41]:
# Parámetros
indicator = 'Urban PM2.5 Exposure'
year = 2015
level = 'city'
country = 'Argentina'

# Llamada a la función
plot_city_or_country_data(
    df=df_combined,
    indicator=indicator,
    year=year,
    level=level,
    countries=[country]
)


In [42]:
# Parámetros
indicator = 'Country PM2.5 Exceedance'
year = 2015
level = 'country'
countries = ['Argentina', 'Brasil', 'Chile', 'Colombia', 'Peru']

# Llamada a la función
plot_city_or_country_data(
    df=df_combined,
    indicator=indicator,
    year=year,
    level=level,
    countries=countries
)


In [20]:
import ijson
import os
import json
import pandas as pd
import unidecode
from decimal import Decimal
# Ruta del archivo JSON
json_path = '../../weather.json'  # Reemplaza con la ruta correcta a tu archivo JSON

# Verificar si el archivo existe
if not os.path.exists(json_path):
    print(f"No se encontró el archivo: {json_path}")
    exit()

# Función para normalizar nombres (si es necesario)
def normalize_name(name):
    if isinstance(name, str):
        return unidecode.unidecode(name).strip().capitalize()
    return name

# Función para convertir objetos Decimal a float
def convert_decimal(obj):
    """
    Recorre el objeto y convierte los valores Decimal a float.
    """
    if isinstance(obj, list):
        return [convert_decimal(item) for item in obj]
    elif isinstance(obj, dict):
        return {k: convert_decimal(v) for k, v in obj.items()}
    elif isinstance(obj, Decimal):
        return float(obj)
    else:
        return obj

# Función para dividir el JSON en 10 archivos pequeños
def split_json_into_chunks(json_path, num_chunks=10, prefix='chunk'):
    """
    Divide un archivo JSON grande en múltiples archivos JSON pequeños.

    Parámetros:
    - json_path: Ruta al archivo JSON.
    - num_chunks: Número de partes en las que dividir el JSON.
    - prefix: Prefijo para los archivos de salida.

    Retorna:
    - Lista de rutas a los archivos divididos.
    """
    # Crear 10 archivos de salida
    output_files = [f'{prefix}_{i+1}.json' for i in range(num_chunks)]
    output_fhs = [open(file, 'w', encoding='utf-8') for file in output_files]

    # Escribir el inicio de una lista en cada archivo
    for fh in output_fhs:
        fh.write('[\n')

    # Contadores para gestionar comas
    first_entry = [True] * num_chunks

    # Abrir el archivo JSON y iterar sobre los objetos
    with open(json_path, 'r', encoding='utf-8') as f:
        # Usando ijson para iterar sobre los objetos en el JSON
        objects = ijson.items(f, 'item')  # Ajusta 'item' según la estructura del JSON

        for idx, obj in enumerate(objects):
            # Asignar al archivo correspondiente de manera round-robin
            chunk_idx = idx % num_chunks
            fh = output_fhs[chunk_idx]

            # Convertir Decimal a float
            obj_converted = convert_decimal(obj)

            # Normalizar los valores de texto si es necesario
            for key, value in obj_converted.items():
                if isinstance(value, str):
                    obj_converted[key] = normalize_name(value)

            # Escribir coma si no es el primer elemento
            if not first_entry[chunk_idx]:
                fh.write(',\n')
            else:
                first_entry[chunk_idx] = False

            # Escribir el objeto JSON
            json.dump(obj_converted, fh, ensure_ascii=False)

    # Escribir el cierre de la lista en cada archivo y cerrar
    for fh in output_fhs:
        fh.write('\n]')
        fh.close()

    return output_files

# Dividir el JSON en 10 partes
print("Dividiendo el JSON en 10 partes...")
chunk_files = split_json_into_chunks(json_path, num_chunks=10, prefix='chunk')
print("División completa.")

# Leer cada chunk en un DataFrame
print("Leyendo los chunks en DataFrames...")
try:
    df1, df2, df3, df4, df5, df6, df7, df8, df9, df10 = [pd.read_json(file) for file in chunk_files]
    print("Lectura de DataFrames completa.")
except ValueError as e:
    print(f"Error al leer uno de los chunks: {e}")
    # Opcional: Imprimir el contenido problemático o manejar el error según sea necesario
    exit()

# Verificar la división
for i, df_part in enumerate([df1, df2, df3, df4, df5, df6, df7, df8, df9, df10], 1):
    print(f"df{i} tiene {len(df_part)} registros.")

# Opcional: Mostrar las primeras filas de df1
print("\nPrimeras filas de df1:")
print(df1.head())

# Opcional: Eliminar los archivos de chunks para liberar espacio
print("Eliminando archivos temporales...")
for file in chunk_files:
    os.remove(file)
print("Archivos temporales eliminados.")


Dividiendo el JSON en 10 partes...
División completa.
Leyendo los chunks en DataFrames...
Lectura de DataFrames completa.
df1 tiene 823509 registros.
df2 tiene 823509 registros.
df3 tiene 823508 registros.
df4 tiene 823508 registros.
df5 tiene 823508 registros.
df6 tiene 823508 registros.
df7 tiene 823508 registros.
df8 tiene 823508 registros.
df9 tiene 823508 registros.
df10 tiene 823508 registros.

Primeras filas de df1:
   AverageTemperature      City         Country  Latitude  Longitude  year  \
0               7.541  Basildon  United kingdom     52.24       0.00  1743   
1               6.425     Neuss         Germany     50.63       6.34  1743   
2               8.248      Rome           Italy     42.59      13.09  1743   
3              -3.005      Tver          Russia     57.05      36.89  1743   
4              -0.106    Guelph          Canada     44.20     -80.50  1743   

   month  
0     11  
1     11  
2     11  
3     11  
4     11  
Eliminando archivos temporales...
Arch

In [21]:
df1

AverageTemperature      City         Country  Latitude  Longitude  \
0                    7.541  Basildon  United kingdom     52.24       0.00   
1                    6.425     Neuss         Germany     50.63       6.34   
2                    8.248      Rome           Italy     42.59      13.09   
3                   -3.005      Tver          Russia     57.05      36.89   
4                   -0.106    Guelph          Canada     44.20     -80.50   
...                    ...       ...             ...       ...        ...   
823504              17.503     Flint   United states     42.59     -82.91   
823505              26.195     Tepic          Mexico     21.70    -104.71   
823506              28.497    Delmas           Haiti     18.48     -72.68   
823507              29.848  Chetumal          Mexico     18.48     -87.89   
823508              24.186   Visalia   United states     36.17    -119.34   

        year  month  
0       1743     11  
1       1743     11  
2       1743     11  
3       1743     11  
4       1743     11  
...      ...    ...  
823504  2013      9  
823505  2013      9  
823506  2013      9  
823507  2013      9  
823508  2013      9  

[823509 rows x 7 columns]

In [30]:
# Vamos a eliminar las entradas cuyos valores de 'year' sean menores a 1983
df1 = df1[df1['year'] > 1993]
# Vamos a eliminar las entrades con valores de temperartura menores a -5
df1 = df1[df1['AverageTemperature'] > -5]
df1

AverageTemperature      City        Country  Latitude  Longitude  \
740629               2.773  Besancon         France     47.42       5.92   
740630               7.690    Foggia          Italy     40.99      14.91   
740631              -2.252      Riga         Latvia     57.05      25.08   
740632              26.545      Tete     Mozambique    -16.87      33.49   
740633              -3.606   Lipetsk         Russia     52.24      39.42   
...                    ...       ...            ...       ...        ...   
823504              17.503     Flint  United states     42.59     -82.91   
823505              26.195     Tepic         Mexico     21.70    -104.71   
823506              28.497    Delmas          Haiti     18.48     -72.68   
823507              29.848  Chetumal         Mexico     18.48     -87.89   
823508              24.186   Visalia  United states     36.17    -119.34   

        year  month  
740629  1994      1  
740630  1994      1  
740631  1994      1  
740632  1994      1  
740633  1994      1  
...      ...    ...  
823504  2013      9  
823505  2013      9  
823506  2013      9  
823507  2013      9  
823508  2013      9  

[80748 rows x 7 columns]

In [31]:
# Creamos un json file con el df1 
df1.to_json('../datasets/reducce_weather.json', orient='records')

In [34]:
import plotly.express as px
px.histogram(df1, x='AverageTemperature', nbins=30, title='Histograma de Temperaturas Promedio')

In [36]:
px.density_mapbox(df1, lat='Latitude', lon='Longitude', z='AverageTemperature', radius=10, center=dict(lat=0, lon=0), zoom=0, title='Mapa de Calor de Temperaturas Promedio')
# mostrar el mapa
px.scatter_geo(df1, lat='Latitude', lon='Longitude', color='AverageTemperature', title='Mapa de Calor de Temperaturas Promedio')

In [47]:
# Un histograma de las temperaturas promedio por pais que inicialmente solo muestre a china, usa y rusia pero que de la posibilidad de checar otros paises
px.histogram(df1, x='AverageTemperature', color='Country', title='Histograma de Temperaturas Promedio por País', facet_col_wrap=3, facet_row_spacing=0.9)
